## Uczenie głębokie – przetwarzanie tekstu – laboratoria
# 3. RNN

In [60]:
!jupyter nbextension enable --py widgetsnbextension

from collections import Counter
import torch
from torchtext.vocab import vocab
from tqdm import tqdm
from ipywidgets import FloatProgress

import pandas as pd
from nltk.tokenize import word_tokenize
from unidecode import unidecode

usage: jupyter [-h] [--version] [--config-dir] [--data-dir] [--runtime-dir]
               [--paths] [--json] [--debug]
               [subcommand]

Jupyter: Interactive Computing

positional arguments:
  subcommand     the subcommand to launch

options:
  -h, --help     show this help message and exit
  --version      show the versions of core jupyter packages and exit
  --config-dir   show Jupyter config dir
  --data-dir     show Jupyter data dir
  --runtime-dir  show Jupyter runtime dir
  --paths        show all Jupyter paths. Add --json for machine-readable
                 format.
  --json         output paths as machine-readable json
  --debug        output debug information about paths

Available subcommands: console dejavu events execute kernel kernelspec lab
labextension labhub migrate nbconvert notebook qtconsole run server
troubleshoot trust

Jupyter command `jupyter-nbextension` not found.


In [61]:
# odczytaj dane treningowe
train = pd.read_csv('train/train.tsv', sep='\t', names=['y', 'x'], header=None)

print("wczytano dane treningowe")
print(train["y"][0], train["x"][0])

print(len(train["y"][0].split(" ")))
print(len(train["x"][0].split(" ")))

# podziel dane treningowe na słowa
# https://www.geeksforgeeks.org/python-word-embedding-using-word2vec/
slowa_train = []
for tekst in train["x"]:
    pom = []
    for slowo in tekst.split(" "):
        #if slowo not in ("<","/s",">","/S","``"):
        pom.append(slowo.lower())
    slowa_train.append(pom)
print("podzielono dane treningowe na słowa")

print(slowa_train[0])
print(len(slowa_train[0]))

wczytano dane treningowe
B-ORG O B-MISC O O O B-MISC O O O B-PER I-PER O B-LOC O O O B-ORG I-ORG O O O O O O B-MISC O O O O O B-MISC O O O O O O O O O O O O O O O B-LOC O O O O B-ORG I-ORG O O O B-PER I-PER O O O O O O O O O O O B-LOC O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG O O O B-PER I-PER I-PER I-PER O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG I-ORG O O O O O O O O O B-ORG O O B-PER I-PER O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-PER O B-MISC O O O O B-LOC O B-LOC O O O O O O O B-MISC I-MISC I-MISC O B-MISC O O O O O O O O B-PER O O O O O O O B-ORG O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-MISC O O B-PER I-PER I-PER O O O B-PER O O B-ORG O O O O O O O O O O O O O O O O O O B-LOC O B-LOC O B-PER O O O O O B-ORG O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-MISC O O O O O O O O O O O O O O O O B-MISC O O O O O O O O O O O O O O O O O O O B-MISC O O O O O O B-MISC O O O O O B-LOC

In [62]:
# odczytaj dane testowe dev-0
test_dev0 = pd.read_csv('dev-0/in.tsv', sep='\t', names=['x'], header=None)

print("wczytano dane testowe dev-0")
print(test_dev0["x"][0])

# podziel dane testowe na słowa
# https://www.geeksforgeeks.org/python-word-embedding-using-word2vec/
slowa_test_dev0 = []
for tekst in test_dev0["x"]:
    pom = []
    for slowo in tekst.split(" "):
        #if slowo not in ("<","/s",">","/S","``"):
        pom.append(slowo.lower())
    slowa_test_dev0.append(pom)
print("podzielono dane treningowe na słowa")

print(slowa_test_dev0[0])
print(len(slowa_test_dev0[0]))

wczytano dane testowe dev-0
CRICKET - LEICESTERSHIRE TAKE OVER AT TOP AFTER INNINGS VICTORY . </S> LONDON 1996-08-30 </S> West Indian all-rounder Phil Simmons took four for 38 on Friday as Leicestershire beat Somerset by an innings and 39 runs in two days to take over at the head of the county championship . </S> Their stay on top , though , may be short-lived as title rivals Essex , Derbyshire and Surrey all closed in on victory while Kent made up for lost time in their rain-affected match against Nottinghamshire . </S> After bowling Somerset out for 83 on the opening morning at Grace Road , Leicestershire extended their first innings by 94 runs before being bowled out for 296 with England discard Andy Caddick taking three for 83 . </S> Trailing by 213 , Somerset got a solid start to their second innings before Simmons stepped in to bundle them out for 174 . </S> Essex , however , look certain to regain their top spot after Nasser Hussain and Peter Such gave them a firm grip on their 

In [63]:
# odczytaj dane testowe A
test_A = pd.read_csv('test-A/in.tsv', sep='\t', names=['x'], header=None)

print("wczytano dane testowe A")
print(test_A["x"][0])

# podziel dane testowe na słowa
# https://www.geeksforgeeks.org/python-word-embedding-using-word2vec/
slowa_test_A = []
for tekst in test_A["x"]:
    pom = []
    for slowo in tekst.split(" "):
        #if slowo not in ("<","/s",">","/S","``"):
        pom.append(slowo.lower())
    slowa_test_A.append(pom)
print("podzielono dane treningowe na słowa")

print(slowa_test_A[0])

wczytano dane testowe A
SOCCER - JAPAN GET LUCKY WIN , CHINA IN SURPRISE DEFEAT . </S> Nadim Ladki </S> AL-AIN , United Arab Emirates 1996-12-06 </S> Japan began the defence of their Asian Cup title with a lucky 2-1 win against Syria in a Group C championship match on Friday . </S> But China saw their luck desert them in the second match of the group , crashing to a surprise 2-0 defeat to newcomers Uzbekistan . </S> China controlled most of the match and saw several chances missed until the 78th minute when Uzbek striker Igor Shkvyrin took advantage of a misdirected defensive header to lob the ball over the advancing Chinese keeper and into an empty net . </S> Oleg Shatskiku made sure of the win in injury time , hitting an unstoppable left foot shot from just outside the area . </S> The former Soviet republic was playing in an Asian Cup finals tie for the first time . </S> Despite winning the Asian Games title two years ago , Uzbekistan are in the finals as outsiders . </S> Two goals f

In [64]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    return vocab(counter, specials=["<unk>", "<pad>", "<bos>", "<eos>"])

In [65]:
v = build_vocab(slowa_train)
v.set_default_index(v["<unk>"])
itos = v.get_itos()  # mapowanie indeksów na tokeny
print(len(itos))  # liczba różnych tokenów w słowniku
print(itos)

21014
['<unk>', '<pad>', '<bos>', '<eos>', 'eu', 'rejects', 'german', 'call', 'to', 'boycott', 'british', 'lamb', '.', '</s>', 'peter', 'blackburn', 'brussels', '1996-08-22', 'the', 'european', 'commission', 'said', 'on', 'thursday', 'it', 'disagreed', 'with', 'advice', 'consumers', 'shun', 'until', 'scientists', 'determine', 'whether', 'mad', 'cow', 'disease', 'can', 'be', 'transmitted', 'sheep', 'germany', "'s", 'representative', 'union', 'veterinary', 'committee', 'werner', 'zwingmann', 'wednesday', 'should', 'buy', 'sheepmeat', 'from', 'countries', 'other', 'than', 'britain', 'scientific', 'was', 'clearer', '"', 'we', 'do', "n't", 'support', 'any', 'such', 'recommendation', 'because', 'see', 'grounds', 'for', ',', 'chief', 'spokesman', 'nikolaus', 'van', 'der', 'pas', 'told', 'a', 'news', 'briefing', 'he', 'further', 'study', 'required', 'and', 'if', 'found', 'that', 'action', 'needed', 'taken', 'by', 'proposal', 'last', 'month', 'farm', 'commissioner', 'franz', 'fischler', 'ban', 

In [66]:
# slownik etykiety - kody etykiet
etykieta_na_kod = {}
licznik = 0
for tekst in train["y"]:
    for etykieta in tekst.split(" "):
        if etykieta not in etykieta_na_kod:
            etykieta_na_kod[etykieta] = licznik
            licznik+=1
print(etykieta_na_kod)

{'B-ORG': 0, 'O': 1, 'B-MISC': 2, 'B-PER': 3, 'I-PER': 4, 'B-LOC': 5, 'I-ORG': 6, 'I-MISC': 7, 'I-LOC': 8}


In [67]:
# podziel etykiety
kody_etykiet_train = []
for tekst in train["y"]:
    pom = []
    for etykieta in tekst.split(" "):
        pom.append(etykieta_na_kod[etykieta])
    kody_etykiet_train.append(pom)
print(kody_etykiet_train[0])

[0, 1, 2, 1, 1, 1, 2, 1, 1, 1, 3, 4, 1, 5, 1, 1, 1, 0, 6, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 0, 6, 1, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 3, 4, 4, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 2, 1, 1, 1, 1, 5, 1, 5, 1, 1, 1, 1, 1, 1, 1, 2, 7, 7, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 3, 4, 4, 1, 1, 1, 3, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 5, 1, 3, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 

In [68]:
# odczytaj etykiety dev-0
labels_dev0 = pd.read_csv('dev-0/expected.tsv', sep='\t', names=['y'], header=None)

print(labels_dev0["y"][0])
print(len(labels_dev0["y"][0].split(" ")))

# podziel etykiety
kody_etykiet_dev0 = []
for tekst in labels_dev0["y"]:
    pom = []
    for etykieta in tekst.split(" "):
        pom.append(etykieta_na_kod[etykieta])
    kody_etykiet_dev0.append(pom)

print(kody_etykiet_dev0[0])
print(len(kody_etykiet_dev0[0]))

O O B-ORG O O O O O O O O O B-LOC O O B-MISC I-MISC O B-PER I-PER O O O O O O O B-ORG O B-ORG O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG O B-ORG O B-ORG O O O O O O B-ORG O O O O O O O O O O B-ORG O O O O B-ORG O O O O O O O O B-LOC I-LOC O B-ORG O O O O O O O O O O O O O O B-LOC O B-PER I-PER O O O O O O O O O O B-ORG O O O O O O O O O B-PER O O O O O O O O O O B-ORG O O O O O O O O O O O B-PER I-PER O B-PER I-PER O O O O O O O O O B-ORG O B-LOC O O B-PER O O O O B-LOC O O O O O O O O O O O O O O O O B-ORG O O O O O O O O O O O O O O O B-ORG O O O O O O O O O B-PER O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-LOC O B-ORG O B-PER I-PER O O O O O B-LOC O O O O O O O O O O O O O O O O O O O O O O O O O B-ORG O O O O O O O B-LOC O B-PER I-PER O O O O B-ORG O O O O O O O O O O O O B-ORG O O O O O O O O O O O O O B-ORG O O O O O O O O O O O O O O O O O O O O B-MISC B-PER I-PER O O O O O B-PER I-PER O O O O B-PER I-PER O O O O B-ORG O O O O O O O O

In [69]:
def data_process(dt):
    # Wektoryzacja dokumentów tekstowych.
    return [
        torch.tensor(
            [v["<bos>"]] + [v[token] for token in document] + [v["<eos>"]],
            dtype=torch.long,
        )
        for document in dt
    ]

def labels_process(dt):
    # Wektoryzacja etykiet (NER)
    return [torch.tensor([0] + document + [0], dtype=torch.long) for document in dt]

In [70]:
train_tokens_ids = data_process(slowa_train)
test_dev0_tokens_ids = data_process(slowa_test_dev0)
test_A_tokens_ids = data_process(slowa_test_A)

train_labels = labels_process(kody_etykiet_train)
test_dev0_labels = labels_process(kody_etykiet_dev0)

In [71]:
print(len(train_tokens_ids), len(train_tokens_ids[0]))
print(len(test_dev0_tokens_ids), len(test_dev0_tokens_ids[0]))
print(len(test_A_tokens_ids), len(test_A_tokens_ids[0]))

print(train_tokens_ids[0])
print(test_dev0_tokens_ids[0])
print(test_A_tokens_ids[0])

945 491
215 458
230 443
tensor([  2,   4,   5,   6,   7,   8,   9,  10,  11,  12,  13,  14,  15,  13,
         16,  17,  13,  18,  19,  20,  21,  22,  23,  24,  25,  26,   6,  27,
          8,  28,   8,  29,  10,  11,  30,  31,  32,  33,  34,  35,  36,  37,
         38,  39,   8,  40,  12,  13,  41,  42,  43,   8,  18,  19,  44,  42,
         45,  46,  47,  48,  21,  22,  49,  28,  50,  51,  52,  53,  54,  55,
         56,  57,  30,  18,  58,  27,  59,  60,  12,  13,  61,  62,  63,  64,
         65,  66,  67,  68,  69,  62,  63,  64,  70,  66,  71,  72,  24,  73,
         61,  18,  20,  42,  74,  75,  76,  77,  78,  79,  80,  81,  82,  83,
         12,  13,  84,  21,  85,  58,  86,  59,  87,  88,  89,  24,  59,  90,
         91,  92,  59,  93,  24,  50,  38,  94,  95,  18,  19,  44,  12,  13,
         84,  21,  81,  96,  97,  98,  95,   4,  99, 100, 101, 102,   8, 103,
         40, 104,  73, 105,  88, 106, 107,  53,  18, 108,  88, 109, 110, 111,
         59,  81, 112, 113,  88, 114, 11

In [72]:
print(len(train_labels), len(train_labels[0]))
print(len(test_dev0_labels), len(test_dev0_labels[0]))

print(train_labels[0])
print(test_dev0_labels[0])

945 491
215 458
tensor([0, 0, 1, 2, 1, 1, 1, 2, 1, 1, 1, 3, 4, 1, 5, 1, 1, 1, 0, 6, 1, 1, 1, 1,
        1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        5, 1, 1, 1, 1, 0, 6, 1, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 0, 1, 1, 1, 3, 4, 4, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 6, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 0, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 2, 1, 1, 1, 1, 5, 1, 5, 1,
        1, 1, 1, 1, 1, 1, 2, 7, 7, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1,
        1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 3, 4, 4, 1, 1, 1, 3, 1, 1, 0, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 5, 1, 3, 1, 1, 1, 1,
        1, 0, 1, 1, 1, 1

In [73]:
def get_scores(y_true, y_pred):
    # Funkcja zwraca precyzję, pokrycie i F1
    acc_score = 0
    tp = 0
    fp = 0
    selected_items = 0
    relevant_items = 0

    for p, t in zip(y_pred, y_true):
        if p == t:
            acc_score += 1

        if p > 0 and p == t:
            tp += 1

        if p > 0:
            selected_items += 1

        if t > 0:
            relevant_items += 1

    if selected_items == 0:
        precision = 1.0
    else:
        precision = tp / selected_items

    if relevant_items == 0:
        recall = 1.0
    else:
        recall = tp / relevant_items

    if precision + recall == 0.0:
        f1 = 0.0
    else:
        f1 = 2 * precision * recall / (precision + recall)

    return precision, recall, f1

In [74]:
num_tags = len(etykieta_na_kod.keys())

class LSTM(torch.nn.Module):

    def __init__(self):
        super(LSTM, self).__init__()
        self.emb = torch.nn.Embedding(len(v.get_itos()), 100)
        self.rec = torch.nn.LSTM(100, 256, 1, batch_first=True)
        self.fc1 = torch.nn.Linear(256, num_tags)

    def forward(self, x):
        emb = torch.relu(self.emb(x))
        lstm_output, (h_n, c_n) = self.rec(emb)
        out_weights = self.fc1(lstm_output)
        return out_weights

In [75]:
def eval_model(dataset_tokens, dataset_labels, model):
    Y_true = []
    Y_pred = []
    for i in tqdm(range(len(dataset_labels))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        tags = list(dataset_labels[i].numpy())
        Y_true += tags

        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        Y_pred += list(Y_batch_pred.numpy())

    return get_scores(Y_true, Y_pred)

In [76]:
lstm = LSTM()
criterion = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(lstm.parameters())
NUM_EPOCHS = 2 #100 #50

In [77]:
for i in range(NUM_EPOCHS):
    lstm.train()
    # for i in tqdm(range(500)):
    for i in tqdm(range(len(train_labels))):
        batch_tokens = train_tokens_ids[i].unsqueeze(0)
        tags = train_labels[i].unsqueeze(1)

        predicted_tags = lstm(batch_tokens)

        optimizer.zero_grad()
        loss = criterion(predicted_tags.squeeze(0), tags.squeeze(1))

        loss.backward()
        optimizer.step()

    lstm.eval()

100%|██████████| 945/945 [00:31<00:00, 30.23it/s]


In [78]:
print(eval_model(test_dev0_tokens_ids, test_dev0_labels, lstm))

100%|██████████| 215/215 [00:00<00:00, 238.89it/s]


(0.8949339082089975, 0.8914443942133815, 0.8931857430003114)


In [79]:
def zwroc_przewidywania(tokeny):
    Y_pred = []
    for i in tqdm(range(len(tokeny))):
        pom1 = lstm(tokeny[i])
        #print(pom1)
        pom2 = torch.argmax(pom1,1)
        #print(pom2)
        pom3 = list(pom2.numpy())
        #print(pom3)
        Y_pred.append(pom3)
    return Y_pred

In [80]:
# i usun bos, eos
def zamien_przewidziane_kody_na_etykiety(przewidywania):
    etykiety = []
    for lista in przewidywania:
        pom = []
        for kod in lista:
            etykieta = None
            for e, k in etykieta_na_kod.items():
                if kod == k:
                    etykieta = e
            pom.append(etykieta)
        etykiety.append(pom)
        del pom[0]
        del pom[-1]
    return etykiety

In [81]:
print(eval_model(test_dev0_tokens_ids, test_dev0_labels, lstm))
przewidywania_kody_test_dev0 = zwroc_przewidywania(test_dev0_tokens_ids)
print(przewidywania_kody_test_dev0[0])
print(len(przewidywania_kody_test_dev0[0]))
przewidywania_etykiety_test_dev0 = zamien_przewidziane_kody_na_etykiety(przewidywania_kody_test_dev0)
print(przewidywania_etykiety_test_dev0[0])
print(len(przewidywania_etykiety_test_dev0[0]))

print(test_dev0_labels[0])
print(len(test_dev0_labels[0]))
print(kody_etykiet_dev0[0])
print(len(kody_etykiet_dev0[0]))

100%|██████████| 215/215 [00:00<00:00, 247.70it/s]


(0.8949339082089975, 0.8914443942133815, 0.8931857430003114)


100%|██████████| 215/215 [00:00<00:00, 239.42it/s]

[0, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 5, 8, 1, 1, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 8, 1, 6, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 5, 1, 1, 1, 1, 1, 6, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 6, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 5, 1, 3, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 0, 1, 1, 1, 1, 

In [82]:
with open("dev-0/out.tsv", "w", encoding="utf-8") as uwu:
    for lista in przewidywania_etykiety_test_dev0:
        for etykieta in lista:
            uwu.write(str(etykieta) + " ")
        uwu.write(str("\n"))

In [83]:
przewidywania_kody_test_A = zwroc_przewidywania(test_A_tokens_ids)
print(przewidywania_kody_test_A[0])
przewidywania_etykiety_test_A = zamien_przewidziane_kody_na_etykiety(przewidywania_kody_test_A)
print(przewidywania_etykiety_test_A[0])

100%|██████████| 230/230 [00:00<00:00, 278.11it/s]

[0, 1, 1, 5, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 5, 8, 1, 5, 1, 5, 8, 6, 6, 1, 5, 1, 1, 1, 1, 1, 1, 7, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 8, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 8, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 0, 8, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 5, 8, 1, 1, 3, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 0, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 8, 1, 1, 1, 1, 1, 5, 

In [84]:
with open("test-A/out.tsv", "w", encoding="utf-8") as uwu:
    for lista in przewidywania_etykiety_test_A:
        for etykieta in lista:
            uwu.write(str(etykieta) + " ")
        uwu.write(str("\n"))

In [85]:
print(eval_model(train_tokens_ids, train_labels, lstm))
przewidywania_kody_test_train = zwroc_przewidywania(train_tokens_ids)
print(przewidywania_kody_test_train[0])
przewidywania_etykiety_test_train = zamien_przewidziane_kody_na_etykiety(przewidywania_kody_test_train)
print(przewidywania_etykiety_test_train[0])

100%|██████████| 945/945 [00:03<00:00, 273.52it/s]


(0.9134328639027648, 0.919004869645874, 0.9162103952046085)


100%|██████████| 945/945 [00:03<00:00, 289.35it/s]


[0, 5, 6, 2, 1, 1, 1, 2, 1, 1, 1, 5, 8, 1, 5, 1, 1, 1, 2, 6, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 2, 6, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 4, 1, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1, 1, 1, 5, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 3, 4, 1, 1, 1, 1, 2, 1, 1, 3, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 5, 1, 3, 1, 1, 1, 1, 1, 0, 1, 1, 4, 1, 1, 4, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 

In [86]:
with open("train/out.tsv", "w", encoding="utf-8") as uwu:
    for lista in przewidywania_etykiety_test_train:
        for etykieta in lista:
            uwu.write(str(etykieta) + " ")
        uwu.write(str("\n"))